# Setting Up unsloth and dependencies

In [1]:
%%capture
import os, importlib.util
!pip install --upgrade -qqq uv
if importlib.util.find_spec("torch") is None or "COLAB_" in "".join(os.environ.keys()):
    try: import numpy; get_numpy = f"numpy=={numpy.__version__}"
    except: get_numpy = "numpy"
    !uv pip install -qqq \
        "torch>=2.8.0" "triton>=3.4.0" {get_numpy} torchvision bitsandbytes "transformers==4.56.2" trackio \
        "unsloth_zoo[base] @ git+https://github.com/unslothai/unsloth-zoo" \
        "unsloth[base] @ git+https://github.com/unslothai/unsloth" \
        git+https://github.com/triton-lang/triton.git@05b2c186c1b6c9a08375389d5efe9cb4c401c075#subdirectory=python/triton_kernels
elif importlib.util.find_spec("unsloth") is None:
    !uv pip install -qqq unsloth trackio
!uv pip install --upgrade --no-deps transformers==4.56.2 tokenizers trl==0.22.2 unsloth unsloth_zoo

# Install the environment and custom openEnv

In [2]:
%%capture
!pip install -qqq fastapi uvicorn requests
!git clone https://github.com/yogesh1801/OpenEnv.git > /dev/null 2>&1
%cd OpenEnv
!git checkout yogesh-julia-env

In [3]:
import subprocess, sys, os
from pathlib import Path
sys.path.insert(0, './src')
working_directory = str(Path.cwd().parent.absolute() / "OpenEnv")

# Setting up a Model using unsloth which we will train

In [12]:
from unsloth import FastLanguageModel
import torch
max_seq_length = 2000
lora_rank = 10
model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/Llama-3.2-3B-Instruct",
    fast_inference = True,
    load_in_4bit = False,
    max_seq_length = max_seq_length,
    gpu_memory_utilization = 0.85,
)

/tmp/ipykernel_2181/209325417.py:1: UserWarning: WARNING: Unsloth should be imported before transformers to ensure all optimizations are applied. Your code may run slower or encounter memory issues without these optimizations.

Please restructure your imports with 'import unsloth' at the top of your file.
  from unsloth import FastLanguageModel


🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
#### Unsloth: `hf_xet==1.1.10` and `ipykernel>6.30.1` breaks progress bars. Disabling for now in XET.
#### Unsloth: To re-enable progress bars, please downgrade to `ipykernel==6.30.1` or wait for a fix to
https://github.com/huggingface/xet-core/issues/526
INFO 10-30 00:38:48 [__init__.py:225] Automatically detected platform rocm.
🦥 Unsloth Zoo will now patch everything to make training faster!
Unsloth: AMD currently is not stable with 4bit bitsandbytes. Disabling for now.


[2025-10-30 00:38:52] INFO vllm_utils.py:752: Unsloth: Patching vLLM


INFO 10-30 00:38:52 [vllm_utils.py:694] Unsloth: Patching vLLM v1 graph capture
Unsloth: Could not patch vLLM V0 graph capture: No module named 'vllm.worker'
==((====))==  Unsloth 2025.10.9: Fast Llama patching. Transformers: 4.56.2. vLLM: 0.11.1rc3.dev39+gf417746ad.rocm700.
   \\   /|    . Num GPUs = 1. Max memory: 191.688 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.9.0a0+git1c57644. ROCm Toolkit: 7.0.51831-a3e329ad8. Triton: 3.4.0
\        /    Bfloat16 = TRUE. FA [Xformers = None. FA2 = True]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: vLLM loading unsloth/Llama-3.2-3B-Instruct with actual GPU utilization = 84.85%
Unsloth: Your GPU has CUDA compute capability 9.4 with VRAM = 191.69 GB.
Unsloth: Using conservativeness = 1.0. Chunked prefill tokens = 2000. Num Sequences = 400.
Unsloth: vLLM's KV Cache can use up to 156.48 GB. Also swap space = 6 GB.
Unsloth: Not an error,

Loading safetensors checkpoint shards:   0% Completed | 0/2 [00:00<?, ?it/s]


...

Capturing CUDA graphs (mixed prefill-decode, PIECEWISE): 100%|██████████████████████████████████████████████████████████████████████████████████████████████| 134/134 [00:07<00:00, 18.14it/s]
Capturing CUDA graphs (decode, FULL): 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 106/106 [00:06<00:00, 17.59it/s]

INFO 10-30 00:39:33 [gpu_model_runner.py:3843] Graph capturing finished in 13 secs, took 0.83 GiB
INFO 10-30 00:39:33 [vllm_utils.py:706] Unsloth: Patched vLLM v1 graph capture finished in 13 secs.


INFO 10-30 00:39:34 [core.py:238] init engine (profile, create kv cache, warmup model) took 35.28 seconds
INFO 10-30 00:39:34 [llm.py:343] Supported tasks: ('generate',)
Unsloth: Just some info: will skip parsing ['pre_feedforward_layernorm', 'norm1', 'ffn_norm', 'q_norm', 'input_layernorm', 'layer_norm1', 'post_layernorm', 'layer_norm2', 'post_feedforward_layernorm', 'norm2', 'k_norm', 'post_attention_layernorm', 'attention_norm']


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Unsloth: Just some info: will skip parsing ['pre_feedforward_layernorm', 'norm1', 'ffn_norm', 'q_norm', 'input_layernorm', 'layer_norm1', 'post_layernorm', 'cross_attn_input_layernorm', 'layer_norm2', 'post_feedforward_layernorm', 'norm2', 'cross_attn_post_attention_layernorm', 'k_norm', 'post_attention_layernorm', 'attention_norm']


In [13]:
model = FastLanguageModel.get_peft_model(
    model,
    r = lora_rank,
    target_modules = [
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj",
    ],
    lora_alpha = lora_rank, # *2 speeds up training
    use_gradient_checkpointing = "unsloth", # Reduces memory usage
    random_state = 3407,
)

Unsloth 2025.10.9 patched 28 layers with 28 QKV layers, 28 O layers and 28 MLP layers.


# Connecting to Env exposed by OpenEnv

In [6]:
from envs.julia_env import JuliaEnv
from envs.julia_env.models import JuliaAction, JuliaObservation

from envs.r_env import REnv
from envs.r_env.models import RAction, RObservation

from envs.ruby_env import RubyEnv
from envs.ruby_env.models import RubyAction, RubyObservation

from envs.zig_env import ZigEnv
from envs.zig_env.models import ZigAction, ZigObservation

1. It is not recommended to directly open a subprocess in python instead expose OpenEnv using a docker container because u know that is the whole point of OpenEnv

### First, build the OpenEnv base image (one-time setup):

```bash
# From OpenEnv root directory
docker build -t openenv-base:latest -f src/core/containers/images/Dockerfile .
```

### Build Julia Environment Image

```bash
# From OpenEnv root directory
docker build -t julia-env:latest -f src/envs/julia_env/server/Dockerfile .
```

### Run the Server

```bash
# Run in background
docker run -d -p 8000:8000 --name julia-env-server julia-env:latest

# OR run in foreground (to see logs)
docker run -p 8000:8000 --name julia-env-server julia-env:latest
```


Note this has to be done in system terminal, since this notebook is hosted inside the docker running these commands in terminal exposed by this notebook is illogical as you cannot run docker inside a docker

# We start Julia training here

In [7]:
port = "8000"
localhost = f"http://localhost:{port}"
# openenv_process = subprocess.Popen(
#     [sys.executable, "-m", "uvicorn", "envs.julia_env.server.app:app", "--host", "0.0.0.0", "--port", port],
#     env = {**os.environ,
#          "PYTHONPATH": f"{working_directory}/src",
#          },
#     stdout = subprocess.PIPE,
#     stderr = subprocess.PIPE,
#     text = True,
#     cwd = working_directory,
# )


# used docker images instead

In [8]:
import requests
import time
print(requests.get(f"{localhost}/health", timeout = 2).content)
openenv_process = JuliaEnv(base_url = localhost)

b'{"status":"healthy"}'


In [9]:
result = openenv_process.reset()
current_state = result.observation
current_state

action = JuliaAction(core_code="""
module MyProject

export add

function add(a::Number, b::Number)
    return a + b
end

end""", test_code = """
using Test
using .MyProject

@testset "Add function Tests" begin
    @test MyProject.add(1, 2) == 3
    @test MyProject.add(1, 2) == 3
    @test Project.add(1, 2) == 3
end
""")

result = openenv_process.step(action)
result

StepResult(observation=JuliaObservation(done=False, reward=None, metadata={}, stdout='Add function Tests: Error During Test at /tmp/tmprp3gjxv3.jl:19\n  Test threw exception\n  Expression: Project.add(1, 2) == 3\n  UndefVarError: `Project` not defined\n  Stacktrace:\n   [1] macro expansion\n     @ ~/.julia/juliaup/julia-1.10.10+0.x64.linux.gnu/share/julia/stdlib/v1.10/Test/src/Test.jl:669 [inlined]\n   [2] macro expansion\n     @ /tmp/tmprp3gjxv3.jl:19 [inlined]\n   [3] macro expansion\n     @ ~/.julia/juliaup/julia-1.10.10+0.x64.linux.gnu/share/julia/stdlib/v1.10/Test/src/Test.jl:1577 [inlined]\n   [4] top-level scope\n     @ /tmp/tmprp3gjxv3.jl:17\nTest Summary:      | Pass  Error  Total  Time\nAdd function Tests |    2      1      3  0.7s\n', stderr='ERROR: LoadError: Some tests did not pass: 2 passed, 0 failed, 1 errored, 0 broken.\nin expression starting at /tmp/tmprp3gjxv3.jl:16\n', exit_code=1, tests_passed=2, tests_failed=1, code_compiles=True), reward=7, done=False)

In [10]:
julia_code_gen_prompt = """
You are a precise and pragmatic Julia programmer.

Write a **single Julia function** that correctly solves the problem described below.

Rules:
- The code must be syntactically correct and runnable as is.
- Do not use arrow functions, ternary operators, or modern syntax that may cause issues.
- Use only the Julia standard library.
- Do **not** wrap the code in a module or add a `main` function.
- Do **not** include any test code in your response.
- Do **not** hardcode specific test cases or outputs — the function must work for general inputs.
- The **function name must exactly match** the one used in the provided tests.
- Respond with **only the Julia function** and nothing else (no explanations, no comments, no extra text)
- The function name must exactly match the one used in the provided tests.
- Return only the Julia function.
- character literal should not contain multiple characters.
- take care of object types and mind that spaces matter in julia so cannot add random spaces

Passing tests and clean, compilable code are rewarded. Hardcoding or failing tests is penalized.

Test Reference (for context only, do not include in the output):
{julia_test}

Code:
""".strip()


In [11]:
import re
def remove_ticks(text):
    text = re.sub(r'^```julia\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [12]:
from trl import GRPOConfig, GRPOTrainer

training_args = GRPOConfig(
    temperature = 1.0,
    learning_rate = 5e-5,
    weight_decay = 0.01,
    warmup_ratio = 0.1,
    lr_scheduler_type = "linear",
    optim = "adamw_8bit",
    logging_steps = 1,
    per_device_train_batch_size = 1,
    gradient_accumulation_steps = 1,
    num_generations = 2,
    max_prompt_length = 2048,
    max_completion_length = 1024,
    num_train_epochs = 1,
    max_steps = 100,
    save_steps = 250,
    report_to = "trackio",
    output_dir = "outputs",

    # For optional training + evaluation
    # fp16_full_eval = True,
    # per_device_eval_batch_size = 4,
    # eval_accumulation_steps = 1,
    # eval_strategy = "steps",
    # eval_steps = 1,
)

Unsloth: We now expect `per_device_train_batch_size` to be a multiple of `num_generations`.
We will change the batch size of 1 to the `num_generations` of 2


In [13]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../julia_trainset.parquet")

df = df[["julia_prompt", "julia_test", "first_test_case"]]
dataset = Dataset.from_pandas(df)

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role" : "system", "content": julia_code_gen_prompt.format(julia_test=x["first_test_case"])},
        {"role" : "user", "content": x["julia_prompt"]},
    ],
})
print(dataset[0])

Map:   0%|          | 0/6326 [00:00<?, ? examples/s]

{'julia_prompt': 'Given a vector of integers, write a function `find_max_sum_subarray(arr::Vector{Int64})` that returns the maximum sum of any contiguous subarray within the vector. A subarray is a continuous portion of the vector. You may assume that the input vector will always have at least one element.', 'julia_test': 'using Test\n\n@testset "my test" begin\n@test find_max_sum_subarray([1, 2, 3, 4, 5]) == 15\n@test find_max_sum_subarray([-1, -2, -3, -4, -5]) == -1\n@test find_max_sum_subarray([1, -2, 3, -4, 5]) == 5\n@test find_max_sum_subarray([-2, 1, -3, 4, -1, 2, 1, -5, 4]) == 6\nend', 'first_test_case': 'using Test\n\n@testset "my test 1" begin\n@test find_max_sum_subarray([1, 2, 3, 4, 5]) == 15\nend', 'prompt': [{'content': 'You are a precise and pragmatic Julia programmer.\n\nWrite a **single Julia function** that correctly solves the problem described below.\n\nRules:\n- The code must be syntactically correct and runnable as is.\n- Do not use arrow functions, ternary operato

In [14]:
def julia_env_reward(completions, **kwargs):
    rewards = []
    test_codes_list = kwargs.get('julia_test', [])

    for i, completion in enumerate(completions):
        response = completion[0]["content"]
        core_code = remove_ticks(response)
        test_code = test_codes_list[i]

        try:
            result = openenv_process.reset()
            action = JuliaAction(core_code=core_code, test_code=test_code)
            result = openenv_process.step(action)

            reward = result.reward if result.reward is not None else 0.0

        except Exception as e:
            print(f"Error for completion {i}:", e)
            reward = 0.0

        rewards.append(reward)

    return rewards

In [15]:
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    remove_unused_columns = False,
    reward_funcs = [julia_env_reward],
    args = training_args,
    train_dataset = dataset,

    # For optional training + evaluation
    # train_dataset = new_dataset["train"],
    # eval_dataset = new_dataset["test"],
)

In [16]:
trainer.train()

The tokenizer has new PAD/BOS/EOS tokens that differ from the model config and generation config. The model config and generation config were aligned accordingly, being updated with the tokenizer's values. Updated tokens: {'pad_token_id': 128004}.
==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 6,326 | Num Epochs = 1 | Total steps = 100
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 1 x 1) = 2
 "-____-"     Trainable parameters = 15,196,160 of 3,227,945,984 (0.47% trained)


* Trackio project initialized: huggingface
* Trackio metrics logged to: /root/.cache/huggingface/trackio


* Created new run: dainty-sunset-0
WARNING 10-29 23:40:45 [processor.py:228] vLLM has deprecated support for supporting different tokenizers for different LoRAs. By default, vLLM uses base model's tokenizer. If you are using a LoRA with its own tokenizer, consider specifying `--tokenizer [lora_path]` to use the LoRA tokenizer.


Unsloth: Will smartly offload gradients to save VRAM!
* Run finished. Uploading logs to Trackio (please wait...)


TrainOutput(global_step=100, training_loss=3.3790673178479836e-06, metrics={'train_runtime': 439.4232, 'train_samples_per_second': 0.455, 'train_steps_per_second': 0.228, 'total_flos': 0.0, 'train_loss': 3.3790673178479836e-06})

# We start R training here

In [17]:
port = "8002"
localhost = f"http://localhost:{port}"
# openenv_process = subprocess.Popen(
#     [sys.executable, "-m", "uvicorn", "envs.r_env.server.app:app", "--host", "0.0.0.0", "--port", port],
#     env = {**os.environ,
#          "PYTHONPATH": f"{working_directory}/src",
#          },
#     stdout = subprocess.PIPE,
#     stderr = subprocess.PIPE,
#     text = True,
#     cwd = working_directory,
# )


# used docker images instead

In [18]:
import requests
import time
print(requests.get(f"{localhost}/health", timeout = 2).content)
openenv_process = REnv(base_url = localhost)

b'{"status":"healthy"}'


In [19]:
action = RAction(
    core_code = """
add <- function(a, b) {
  return(a + b)
}
""",
    test_code = """
library(testthat)

test_that("add works for positive numbers", {
  expect_equal(add(1, 2), 3)
})

test_that("add works for zeros", {
  expect_equal(add(0, 0), 0)
})

test_that("add works for negative numbers", {
  expect_equal(add(-1, -2), -3)
})
"""
)

result = openenv_process.step(action)
result

StepResult(observation=RObservation(done=False, reward=None, metadata={}, stdout='\n══ Testing tmpe7t6g79c.R ═══════════════════════════════════════════════════════\n\n[ FAIL 0 | WARN 0 | SKIP 0 | PASS 0 ]\n[ FAIL 0 | WARN 0 | SKIP 0 | PASS 1 ]\n[ FAIL 0 | WARN 0 | SKIP 0 | PASS 2 ]\n[ FAIL 0 | WARN 0 | SKIP 0 | PASS 3 ] Done!\n', stderr='', exit_code=0, tests_passed=3, tests_failed=0, code_compiles=True), reward=13, done=False)

In [6]:
R_code_gen_prompt = """
You are a precise and pragmatic R programmer.
Write a **single R function** that correctly solves the problem described below.
Rules:
- The code must be syntactically correct and runnable as is.
- Use traditional R function syntax with proper braces and return statements.
- Use only base R (no external packages).
- Do **not** wrap the code in additional scaffolding or add a `main` function.
- Do **not** include any test code in your response.
- Do **not** hardcode specific test cases or outputs — the function must work for general inputs.
- The **function name must exactly match** the one used in the provided tests.
- Respond with **only the R function** and nothing else (no explanations, no comments, no extra text)
- The function name must exactly match the one used in the provided tests.
- Return only the R function.
- Use proper R syntax: assignment with <-, proper vectorization, and correct indexing (1-based).
- Pay attention to data types: use as.integer(), as.numeric(), as.character() when needed.
- Remember R is 1-indexed, not 0-indexed.
Passing tests and clean, runnable code are rewarded. Hardcoding or failing tests is penalized.
Test Reference (for context only, do not include in the output):
{r_test}
Code:
""".strip()

In [21]:
import re
def remove_ticks(text):
    text = re.sub(r'^```r\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [22]:
def r_env_reward(completions, **kwargs):
    rewards = []
    test_codes_list = kwargs.get('r_test', [])

    for i, completion in enumerate(completions):
        response = completion[0]["content"]
        core_code = remove_ticks(response)
        test_code = test_codes_list[i]
        try:
            result = openenv_process.reset()
            action = RAction(core_code=core_code, test_code=test_code)
            result = openenv_process.step(action)

            reward = result.reward if result.reward is not None else 0.0

        except Exception as e:
            print(f"Error for completion {i}:", e)
            reward = 0.0

        rewards.append(reward)

    return rewards

In [23]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../r_trainset.parquet")

df = df[["r_prompt", "r_test", "first_test_case"]]
dataset = Dataset.from_pandas(df)

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role" : "system", "content": R_code_gen_prompt.format(r_test=x["first_test_case"])},
        {"role" : "user", "content": x["r_prompt"]},
    ],
})
print(dataset[0])

Map:   0%|          | 0/6406 [00:00<?, ? examples/s]

{'r_prompt': 'You are tasked with implementing a function that checks the uniqueness of a username and an email for a user registration system. The function should take two parameters: `username` and `email`, and check them against a predefined list of already registered usernames and emails. If both the username and email are not already registered, the function should return a message indicating that they can be used. If either the username or email is already in use, the function should return a message indicating that they are not available. Implement the function `is_unique(username, email)` to fulfill these requirements.', 'r_test': 'library(testthat)\ntest_that("is_unique returns available for new username and email", {\n  expect_equal(is_unique("newuser", "newuser@example.com"), "Username and email can be used.")\n})\ntest_that("is_unique returns not available for existing username", {\n  expect_equal(is_unique("user1", "newuser@example.com"), "Username or email is not availabl

In [24]:
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    remove_unused_columns = False,
    reward_funcs = [r_env_reward],
    args = training_args,
    train_dataset = dataset,

    # For optional training + evaluation
    # train_dataset = new_dataset["train"],
    # eval_dataset = new_dataset["test"],
)

In [25]:
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 6,406 | Num Epochs = 1 | Total steps = 100
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 1 x 1) = 2
 "-____-"     Trainable parameters = 15,196,160 of 3,227,945,984 (0.47% trained)


* Trackio project initialized: huggingface
* Trackio metrics logged to: /root/.cache/huggingface/trackio


* Created new run: brave-forest-1


* Run finished. Uploading logs to Trackio (please wait...)


TrainOutput(global_step=100, training_loss=1.7680947508651458e-05, metrics={'train_runtime': 214.8682, 'train_samples_per_second': 0.931, 'train_steps_per_second': 0.465, 'total_flos': 0.0, 'train_loss': 1.7680947508651458e-05})

# We start Ruby training here

In [26]:
port = "8003"
localhost = f"http://localhost:{port}"
# openenv_process = subprocess.Popen(
#     [sys.executable, "-m", "uvicorn", "envs.ruby_env.server.app:app", "--host", "0.0.0.0", "--port", port],
#     env = {**os.environ,
#          "PYTHONPATH": f"{working_directory}/src",
#          },
#     stdout = subprocess.PIPE,
#     stderr = subprocess.PIPE,
#     text = True,
#     cwd = working_directory,
# )


# used docker images instead

In [27]:
import requests
import time
print(requests.get(f"{localhost}/health", timeout = 2).content)
openenv_process = RubyEnv(base_url = localhost)

b'{"status":"healthy"}'


In [28]:
action = RubyAction(
    core_code = """
def add_nums(a, b)
  a + b
end
""",
    test_code = """
require 'test/unit'

class TestAddNums < Test::Unit::TestCase
  def test_add_positive_numbers
    assert_equal(8, add_nums(5, 3))
  end

  def test_add_negative_numbers
    assert_equal(-8, add_nums(-5, -3))
  end

  def test_add_zero
    assert_equal(5, add_nums(5, 0))
  end

  def test_add_mixed_signs
    assert_equal(2, add_nums(5, -3))
  end
end
"""
)

result = openenv_process.step(action)
result

StepResult(observation=RubyObservation(done=False, reward=None, metadata={}, stdout='Loaded suite /tmp/tmpcj5i_nk8\nStarted\nFinished in 0.000273646 seconds.\n-------------------------------------------------------------------------------\n4 tests, 4 assertions, 0 failures, 0 errors, 0 pendings, 0 omissions, 0 notifications\n100% passed\n-------------------------------------------------------------------------------\n14617.43 tests/s, 14617.43 assertions/s\n', stderr='', exit_code=0, tests_passed=4, tests_failed=0, code_compiles=True), reward=16, done=False)

In [7]:
Ruby_code_gen_prompt = """
You are a precise and pragmatic Ruby programmer.
Write a **single Ruby function** that correctly solves the problem described below.

Rules:
- The code must be syntactically correct and runnable as is.
- Use standard Ruby function syntax:
    def function_name(args)
      ...
    end
- Use only base Ruby (no external libraries or gems).
- Do **not** wrap the code in any scaffolding, classes, or a `main` function.
- Do **not** include any test code, print statements, or comments.
- Do **not** hardcode specific test cases or outputs — the function must work for general inputs.
- The **function name must exactly match** the one used in the provided tests.
- Return only the Ruby function and nothing else (no explanations, no extra text).
- Pay attention to correct Ruby syntax: use `=`, `.to_i`, `.to_f`, `.to_s` for conversions.
- Arrays and strings in Ruby are 0-indexed.
- Ensure the function works correctly for general input cases.

Test Reference (for context only, do not include in the output):
{ruby_test}

Code:
""".strip()

In [30]:
import re
def remove_ticks(text):
    text = re.sub(r'^```ruby\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [31]:
def ruby_env_reward(completions, **kwargs):
    rewards = []
    test_codes_list = kwargs.get('ruby_test', [])

    for i, completion in enumerate(completions):
        response = completion[0]["content"]
        core_code = remove_ticks(response)
        test_code = test_codes_list[i]
        try:
            result = openenv_process.reset()
            action = RubyAction(core_code=core_code, test_code=test_code)
            result = openenv_process.step(action)

            reward = result.reward if result.reward is not None else 0.0

        except Exception as e:
            print(f"Error for completion {i}:", e)
            reward = 0.0

        rewards.append(reward)

    return rewards

In [32]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../ruby_trainset.parquet")

df = df[["ruby_prompt", "ruby_test", "first_test_case"]]
dataset = Dataset.from_pandas(df)

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role" : "system", "content": Ruby_code_gen_prompt.format(ruby_test=x["first_test_case"])},
        {"role" : "user", "content": x["ruby_prompt"]},
    ],
})
print(dataset[0])

Map:   0%|          | 0/4715 [00:00<?, ? examples/s]

{'ruby_prompt': "You are tasked with creating a function that simulates a search operation on a web application. The function should take a search term as input and return a message indicating the number of results found for that search term. The expected behavior is that if the search term is 'ruby', the function should return 'Showing results for ruby: 10 results found'. For any other search term, it should return 'Showing results for {search_term}: 0 results found'. Your function should only handle the search term input and return the respective message without any external dependencies or database interactions.", 'ruby_test': "require 'test/unit'\n\nclass TestSearchResults < Test::Unit::TestCase\n  def test_search_for_ruby\n    assert_equal 'Showing results for ruby: 10 results found', search_results('ruby')\n  end\n\n  def test_search_for_ruby_case_insensitive\n    assert_equal 'Showing results for RUBY: 10 results found', search_results('RUBY')\n  end\n\n  def test_search_for_non

In [33]:
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    remove_unused_columns = False,
    reward_funcs = [ruby_env_reward],
    args = training_args,
    train_dataset = dataset,

    # For optional training + evaluation
    # train_dataset = new_dataset["train"],
    # eval_dataset = new_dataset["test"],
)

In [34]:
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 4,715 | Num Epochs = 1 | Total steps = 100
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 1 x 1) = 2
 "-____-"     Trainable parameters = 15,196,160 of 3,227,945,984 (0.47% trained)


* Trackio project initialized: huggingface
* Trackio metrics logged to: /root/.cache/huggingface/trackio


* Created new run: calm-river-2


* Run finished. Uploading logs to Trackio (please wait...)


TrainOutput(global_step=100, training_loss=5.177777451201848e-06, metrics={'train_runtime': 131.2295, 'train_samples_per_second': 1.524, 'train_steps_per_second': 0.762, 'total_flos': 0.0, 'train_loss': 5.177777451201848e-06})

# We start Zig training here

In [35]:
port = "8004"
localhost = f"http://localhost:{port}"
# openenv_process = subprocess.Popen(
#     [sys.executable, "-m", "uvicorn", "envs.zig_env.server.app:app", "--host", "0.0.0.0", "--port", port],
#     env = {**os.environ,
#          "PYTHONPATH": f"{working_directory}/src",
#          },
#     stdout = subprocess.PIPE,
#     stderr = subprocess.PIPE,
#     text = True,
#     cwd = working_directory,
# )


# used docker images instead

In [36]:
import requests
import time
print(requests.get(f"{localhost}/health", timeout = 2).content)
openenv_process = ZigEnv(base_url = localhost)

b'{"status":"healthy"}'


In [37]:
result = openenv_process.reset()
current_state = result.observation
current_state

action = ZigAction(
    core_code="""const std = @import("std");

pub fn add(a: i32, b: i32) i32 {
    return a + b;
}""",
    test_code="""
const testing = std.testing;

test "add with positive numbers" {
    try testing.expectEqual(@as(i32, 3), add(1, 2));
}

test "add with negative numbers" {
    try testing.expectEqual(@as(i32, -1), add(-3, 2));
}

test "add with zeros" {
    try testing.expectEqual(@as(i32, 0), add(0, 0));
}"""
)

result = openenv_process.step(action)
result

StepResult(observation=ZigObservation(done=False, reward=None, metadata={}, stdout='', stderr='1/3 main.test.add with positive numbers...OK\n2/3 main.test.add with negative numbers...OK\n3/3 main.test.add with zeros...OK\nAll 3 tests passed.\n', exit_code=0, tests_passed=3, tests_failed=0, code_compiles=True), reward=13, done=False)

In [8]:
zig_code_gen_prompt = """
You are a precise and pragmatic Zig programmer.
Write a **single Zig function** that correctly solves the problem described below.

Rules:
- The code must be syntactically correct, compilable, and runnable as is.
- Use standard Zig syntax with explicit types and return statements.
- Use only the Zig standard library (no external packages).
- Do **not** wrap the code in a module, struct, or add a `main` function.
- Do **not** include any test code, print statements, or comments.
- Do **not** hardcode specific test cases or outputs — the function must work for general inputs.
- The **function name must exactly match** the one used in the provided tests.
- Return only the Zig function and nothing else (no explanations, no extra text).
- Use correct Zig types (e.g., i32, i64, f32, f64, []const u8, bool, etc.).
- Include proper error handling with `try`/`catch` or optional types if appropriate.
- Functions must end with an explicit `return` statement.
- Follow Zig conventions: snake_case function names and consistent indentation.

Passing tests and clean, compilable code are rewarded. Hardcoding or failing tests is penalized.

Test Reference (for context only, do not include in the output):
{zig_test}

Code:
""".strip()


In [39]:
import re
def remove_ticks(text):
    text = re.sub(r'^```zig\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [40]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../zig_trainset.parquet")

df = df[["zig_prompt", "zig_test", "first_test_case"]]
dataset = Dataset.from_pandas(df)

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role" : "system", "content": zig_code_gen_prompt.format(zig_test=x["first_test_case"])},
        {"role" : "user", "content": x["zig_prompt"]},
    ],
})
print(dataset[0])

Map:   0%|          | 0/723 [00:00<?, ? examples/s]

{'zig_prompt': "Given a string representing a URL, implement a function `check_url` that returns `true` if the URL is valid and uses secure HTTPS communication. Otherwise, return `true` or `false`. A URL is considered valid if it is properly formatted, and it must start with 'https://'. You do not need to check if the URL points to an active website. \n\nHere is the function signature: \n```zig\nfn check_url(url: []const u8) bool {\n    // implementation\n}\n```", 'zig_test': 'const testing = std.testing;\n\ntest "check_url with valid https URL" {\n    try testing.expectEqual(@as(bool, true), check_url("https://www.example.com"));\n}\n\ntest "check_url with invalid http URL" {\n    try testing.expectEqual(@as(bool, false), check_url("http://www.example.com"));\n}\n\ntest "check_url with URL that does not start with https" {\n    try testing.expectEqual(@as(bool, false), check_url("www.example.com"));\n}\n\ntest "check_url with empty string" {\n    try testing.expectEqual(@as(bool, fals

In [41]:
def zig_env_reward(completions, **kwargs):
    rewards = []
    test_codes_list = kwargs.get('zig_test', [])

    for i, completion in enumerate(completions):
        response = completion[0]["content"]
        core_code = remove_ticks(response)
        test_code = test_codes_list[i]

        try:
            result = openenv_process.reset()
            action = ZigAction(core_code=core_code, test_code=test_code)
            result = openenv_process.step(action)

            reward = result.reward if result.reward is not None else 0.0

        except Exception as e:
            print(f"Error for completion {i}:", e)
            reward = 0.0

        rewards.append(reward)

    return rewards

In [42]:
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    remove_unused_columns = False,
    reward_funcs = [zig_env_reward],
    args = training_args,
    train_dataset = dataset,

    # For optional training + evaluation
    # train_dataset = new_dataset["train"],
    # eval_dataset = new_dataset["test"],
)

In [43]:
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 723 | Num Epochs = 1 | Total steps = 100
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 1 x 1) = 2
 "-____-"     Trainable parameters = 15,196,160 of 3,227,945,984 (0.47% trained)


* Trackio project initialized: huggingface
* Trackio metrics logged to: /root/.cache/huggingface/trackio


* Created new run: eager-mountain-3


* Run finished. Uploading logs to Trackio (please wait...)


TrainOutput(global_step=100, training_loss=2.84844899876191e-05, metrics={'train_runtime': 235.6175, 'train_samples_per_second': 0.849, 'train_steps_per_second': 0.424, 'total_flos': 0.0, 'train_loss': 2.84844899876191e-05})

# Post training and inferencing

In [44]:
model.save_lora("grpo_saved_lora_unified")

In [45]:
from safetensors import safe_open

tensors = {}
with safe_open("grpo_saved_lora_unified/adapter_model.safetensors", framework = "pt") as f:
    # Verify both A and B are non zero
    for key in f.keys():
        tensor = f.get_tensor(key)
        n_zeros = (tensor == 0).sum() / tensor.numel()
        assert(n_zeros.item() != tensor.numel())

# Julia

In [46]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../julia_testset.parquet")

df = df[["julia_prompt", "julia_test", "task_id", "first_test_case"]]
dataset = Dataset.from_pandas(df)

MAX_LEN = 2000

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role": "system", "content": julia_code_gen_prompt.format(julia_test=x["first_test_case"])[:MAX_LEN]},
        {"role": "user", "content": x["julia_prompt"][:MAX_LEN]},
    ],
})

Map:   0%|          | 0/2712 [00:00<?, ? examples/s]

In [47]:
import re
def remove_ticks(text):
    text = re.sub(r'^```julia\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [48]:
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []

for i in range(len(dataset)):
    task_id = dataset[i]["task_id"]
    julia_test = dataset[i]["julia_test"]
    message = dataset[i]["prompt"]
    message[1]

    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )

    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=None,
    )

    julia_code = response[0].outputs[0].text
    julia_code = remove_ticks(julia_code)

    results.append({
        "task_id": task_id,
        "julia_code": julia_code,
        "julia_test": julia_test
    })

result_df = pd.DataFrame(results)
result_df.to_parquet("julia_code_output_smaller_model_baseline.parquet", index=False)

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

In [49]:
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []

for i in range(len(dataset)):
    task_id = dataset[i]["task_id"]
    julia_test = dataset[i]["julia_test"]
    message = dataset[i]["prompt"]
    message[1]

    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )

    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=model.load_lora("grpo_saved_lora_unified"),
    )

    julia_code = response[0].outputs[0].text
    julia_code = remove_ticks(julia_code)

    results.append({
        "task_id": task_id,
        "julia_code": julia_code,
        "julia_test": julia_test
    })

result_df = pd.DataFrame(results)
result_df.to_parquet("julia_code_output_smaller_model.parquet", index=False)

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

# R

In [14]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../r_testset.parquet")

df = df[["r_prompt", "r_test", "task_id", "first_test_case"]]
dataset = Dataset.from_pandas(df)

MAX_LEN = 2000

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role": "system", "content": R_code_gen_prompt.format(r_test=x["first_test_case"])[:MAX_LEN]},
        {"role": "user", "content": x["r_prompt"][:MAX_LEN]},
    ],
})

Map:   0%|          | 0/2746 [00:00<?, ? examples/s]

In [15]:
import re
def remove_ticks(text):
    text = re.sub(r'^```r\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [16]:
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []

for i in range(min(500, len(dataset))):
    task_id = dataset[i]["task_id"]
    r_test = dataset[i]["r_test"]
    message = dataset[i]["prompt"]
    message[1]

    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )

    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=None,
    )

    r_code = response[0].outputs[0].text
    r_code = remove_ticks(r_code)

    results.append({
        "task_id": task_id,
        "r_code": r_code,
        "r_test": r_test
    })

result_df = pd.DataFrame(results)
result_df.to_parquet("r_code_output_smaller_model_baseline.parquet", index=False)

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

In [17]:
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []

for i in range(min(500, len(dataset))):
    task_id = dataset[i]["task_id"]
    r_test = dataset[i]["r_test"]
    message = dataset[i]["prompt"]
    message[1]

    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )

    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=model.load_lora("grpo_saved_lora_unified"),
    )

    r_code = response[0].outputs[0].text
    r_code = remove_ticks(r_code)

    results.append({
        "task_id": task_id,
        "r_code": r_code,
        "r_test": r_test
    })

result_df = pd.DataFrame(results)
result_df.to_parquet("r_code_output_smaller_model.parquet", index=False)

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

WARNING 10-30 00:43:03 [processor.py:228] vLLM has deprecated support for supporting different tokenizers for different LoRAs. By default, vLLM uses base model's tokenizer. If you are using a LoRA with its own tokenizer, consider specifying `--tokenizer [lora_path]` to use the LoRA tokenizer.


Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

...

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

# Ruby

In [18]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../ruby_testset.parquet")

df = df[["ruby_prompt", "ruby_test", "task_id", "first_test_case"]]
dataset = Dataset.from_pandas(df)

MAX_LEN = 2000

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role": "system", "content": Ruby_code_gen_prompt.format(ruby_test=x["first_test_case"])[:MAX_LEN]},
        {"role": "user", "content": x["ruby_prompt"][:MAX_LEN]},
    ],
})

Map:   0%|          | 0/2021 [00:00<?, ? examples/s]

In [19]:
import re
def remove_ticks(text):
    text = re.sub(r'^```ruby\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [20]:
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []

for i in range(min(500, len(dataset))):
    task_id = dataset[i]["task_id"]
    ruby_test = dataset[i]["ruby_test"]
    message = dataset[i]["prompt"]
    message[1]

    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )

    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=None,
    )

    ruby_code = response[0].outputs[0].text
    ruby_code = remove_ticks(ruby_code)

    results.append({
        "task_id": task_id,
        "ruby_code": ruby_code,
        "ruby_test": ruby_test
    })

result_df = pd.DataFrame(results)
result_df.to_parquet("ruby_code_output_smaller_model_baseline.parquet", index=False)

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

In [21]:
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []

for i in range(min(500, len(dataset))):
    task_id = dataset[i]["task_id"]
    ruby_test = dataset[i]["ruby_test"]
    message = dataset[i]["prompt"]
    message[1]

    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )

    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=model.load_lora("grpo_saved_lora_unified"),
    )

    ruby_code = response[0].outputs[0].text
    ruby_code = remove_ticks(ruby_code)

    results.append({
        "task_id": task_id,
        "ruby_code": ruby_code,
        "ruby_test": ruby_test
    })

result_df = pd.DataFrame(results)
result_df.to_parquet("ruby_code_output_smaller_model.parquet", index=False)

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

# Zig

In [22]:
import pandas as pd
from datasets import Dataset

df = pd.read_parquet("../zig_testset.parquet")

df = df[["zig_prompt", "zig_test", "task_id", "first_test_case"]]
dataset = Dataset.from_pandas(df)

MAX_LEN = 2000

dataset = dataset.map(lambda x: {
    "prompt": [
        {"role": "system", "content": zig_code_gen_prompt.format(zig_test=x["first_test_case"])[:MAX_LEN]},
        {"role": "user", "content": x["zig_prompt"][:MAX_LEN]},
    ],
})

dataset[0]

Map:   0%|          | 0/311 [00:00<?, ? examples/s]

{'zig_prompt': "Write a function `createWebServer` that takes a `host` []const u8 and a `port` i32 as parameters and returns a []const u8 that indicates the web server is set to run on the specified host and port. The output string should be formatted as 'Web server running on {host}:{port}'.",
 'zig_test': 'const testing = std.testing;\n\ntest "createWebServer with localhost and port 8080" {\n    try testing.expectEqualStrings("Web server running on localhost:8080", createWebServer("localhost", 8080));\n}\n\ntest "createWebServer with custom host and port" {\n    try testing.expectEqualStrings("Web server running on example.com:1234", createWebServer("example.com", 1234));\n}\n\ntest "createWebServer with empty host" {\n    try testing.expectEqualStrings("Web server running on :8080", createWebServer("", 8080));\n}\n\ntest "createWebServer with zero port" {\n    try testing.expectEqualStrings("Web server running on localhost:0", createWebServer("localhost", 0));\n}',
 'task_id': 'task

In [23]:
import re
def remove_ticks(text):
    text = re.sub(r'^```zig\s*\n?', '', text, flags=re.IGNORECASE)
    text = re.sub(r'\n?```\s*$', '', text)

    return text

In [25]:
import pandas as pd
from tqdm import tqdm
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []
for i in tqdm(range(min(500, len(dataset))), desc="Generating Zig Code"):
    task_id = dataset[i]["task_id"]
    zig_test = dataset[i]["zig_test"]
    message = dataset[i]["prompt"]
    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )
    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=None,
    )
    zig_code = response[0].outputs[0].text
    zig_code = remove_ticks(zig_code)
    results.append({
        "task_id": task_id,
        "zig_code": zig_code,
        "zig_test": zig_test
    })

# Save results to parquet
result_df = pd.DataFrame(results)
result_df.to_parquet("zig_code_output_smaller_model_baseline.parquet", index=False)
print("✅ Zig code generation completed and saved to zig_code_output_smaller_model.parquet")

Generating Zig Code:   0%|                                                                                                                                            | 0/311 [00:00<?, ?it/s]

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Generating Zig Code:   0%|▍                                                                                                                                   | 1/311 [00:00<01:21,  3.79it/s]

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Generating Zig Code: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌| 310/311 [01:52<00:00,  3.34it/s]

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Generating Zig Code: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 311/311 [01:53<00:00,  2.74it/s]

✅ Zig code generation completed and saved to zig_code_output_smaller_model.parquet


In [26]:
import pandas as pd
from tqdm import tqdm
from vllm import SamplingParams

sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)

results = []
for i in tqdm(range(min(500, len(dataset))), desc="Generating Zig Code"):
    task_id = dataset[i]["task_id"]
    zig_test = dataset[i]["zig_test"]
    message = dataset[i]["prompt"]
    text = tokenizer.apply_chat_template(
        message,
        add_generation_prompt=True,
        tokenize=False,
    )
    response = model.fast_generate(
        text,
        sampling_params=sampling_params,
        lora_request=model.load_lora("grpo_saved_lora_unified"),
    )
    zig_code = response[0].outputs[0].text
    zig_code = remove_ticks(zig_code)
    results.append({
        "task_id": task_id,
        "zig_code": zig_code,
        "zig_test": zig_test
    })

# Save results to parquet
result_df = pd.DataFrame(results)
result_df.to_parquet("zig_code_output_smaller_model.parquet", index=False)
print("✅ Zig code generation completed and saved to zig_code_output_smaller_model.parquet")

Generating Zig Code:   0%|                                                                                                                                            | 0/311 [00:00<?, ?it/s]

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Generating Zig Code:   0%|▍                                                                                                                                   | 1/311 [00:00<02:03,  2.51it/s]

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

...

Generating Zig Code: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌| 310/311 [03:34<00:00,  1.58it/s]

Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|                                                                                      …

Generating Zig Code: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 311/311 [03:35<00:00,  1.44it/s]

✅ Zig code generation completed and saved to zig_code_output_smaller_model.parquet
